# Selecting values from Tiff

We start of by making the necessary imports

In [1]:
import pandas as pd # General data handling library -> aimed more at data science / flat matrices (multi indexing gets confusing)
import pandas_profiling # Adds tools for dataset
import numpy # Array manipulation library

import xarray as xr # Newish multidimension labbeled data manipulation library -> good with netcdf files also has rasterio importer for geotiffs
import hvplot.xarray # Add interactive plotting to xarray

In [38]:
GEOTIFFNAME = 'SSSjfm_IPSL4X_ModPg_180x360.tif'
POINTSFILENAME = 'points.xlsx'

## Load Points / Coordinates
So lets first import start by loading the data in.

Pandas has some handy tools for reading excel files natively.

<div class='alert alert-info'>
    These points don't have to come from a file you can adapt the notebook to write them inline or even do it iteractively by clicking on the grid
</div>

In [ ]:
points = pd.read_excel(POINTSFILENAME)
points

Lets take a look at our data

In [5]:
points.profile_report()

/opt/conda/envs/python/lib/python3.7/site-packages/pandas/core/frame.py:4446: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


There are lots of no data values there must have been some problems with saving the file.

Lets clean that up

In [4]:
points = points.dropna()
points

Location__  POINT_X (long)  POINT_Y (lat)
0        Slovakia_Povanska_Bystrica_Manin       26.634083      39.347406
1              Ukraine_Kolomya_Marmarosch       32.286813      39.120745
2      Offshore W France_Armorican margin        3.730341      37.250708
3                W Switzerland_Neuch├ótel       16.999813      36.879194
4              North Atlantic_Flemish Cap       -0.138294      36.825156
..                                    ...             ...            ...
95                   Oman_Dhofar_Sallalah       39.952266     -14.264244
96            Somalia_Bosaso & Ras Antara       36.596985     -15.086789
97                              Iran_Khur       47.983603     -16.272461
98  Chili_Atacama_Copiapo_Cerro Pajonales      -37.435439     -28.520510
99                  Tanzania_Lindi region       20.439409     -33.150369

[100 rows x 3 columns]

## Import the geotiffs

Apparently the default library for importing geotiffs is `rasterio`. `xarray` have built on top of this library to be able to import geotiffs directly. So this isn't the most "pure" way but as we use `xarray` a lot in different places I believe this is the _best_ way.

In [6]:
# In this example I am reading a file with (time, x, y) as dimensions
xarr = xr.open_rasterio(GEOTIFFNAME)
xarr

<xarray.DataArray (band: 1, y: 180, x: 360)>
array([[[2.015074e+01, 2.014978e+01, ..., 2.015263e+01, 2.015169e+01],
        [2.017789e+01, 2.017660e+01, ..., 2.017960e+01, 2.017917e+01],
        ...,
        [1.000000e+20, 1.000000e+20, ..., 1.000000e+20, 1.000000e+20],
        [1.000000e+20, 1.000000e+20, ..., 1.000000e+20, 1.000000e+20]]],
      dtype=float32)
Coordinates:
  * band     (band) int64 1
  * y        (y) float64 89.5 88.5 87.5 86.5 85.5 ... -86.5 -87.5 -88.5 -89.5
  * x        (x) float64 -179.5 -178.5 -177.5 -176.5 ... 176.5 177.5 178.5 179.5
Attributes:
    transform:      (1.0, 0.0, -180.0, 0.0, -1.0, 90.0)
    crs:            +init=epsg:4326
    res:            (1.0, 1.0)
    is_tiled:       1
    nodatavals:     (1e+20,)
    scales:         (1.0,)
    offsets:        (0.0,)
    AREA_OR_POINT:  Area

This has loaded the file as a `xarray.DataArray` we can see it has 3 coordinates, `x`, `y` and `band` in our case there is only one band so we are just going to remove it

In [22]:
# Slice one of the bands
#.      band, y, x -> see dimensions above
img = xarr[0, :, :] 
# Lets take a look at our image
img.hvplot.image()

:Image   [x,y]   (value)

### Selecting points
We can select a point with `.sel` we use the `method='nearest'` to get the nearest value to a point if it doesn't exisit

In [23]:
img.sel(x=0.1, y=0.1, method="nearest")

<xarray.DataArray ()>
array(1.e+20, dtype=float32)
Coordinates:
    band     int64 1
    y        float64 0.5
    x        float64 0.5
Attributes:
    transform:      (1.0, 0.0, -180.0, 0.0, -1.0, 90.0)
    crs:            +init=epsg:4326
    res:            (1.0, 1.0)
    is_tiled:       1
    nodatavals:     (1e+20,)
    scales:         (1.0,)
    offsets:        (0.0,)
    AREA_OR_POINT:  Area

### Lets try and get all the points

In [9]:
points

Location__  POINT_X (long)  POINT_Y (lat)
0        Slovakia_Povanska_Bystrica_Manin       26.634083      39.347406
1              Ukraine_Kolomya_Marmarosch       32.286813      39.120745
2      Offshore W France_Armorican margin        3.730341      37.250708
3                W Switzerland_Neuch├ótel       16.999813      36.879194
4              North Atlantic_Flemish Cap       -0.138294      36.825156
..                                    ...             ...            ...
95                   Oman_Dhofar_Sallalah       39.952266     -14.264244
96            Somalia_Bosaso & Ras Antara       36.596985     -15.086789
97                              Iran_Khur       47.983603     -16.272461
98  Chili_Atacama_Copiapo_Cerro Pajonales      -37.435439     -28.520510
99                  Tanzania_Lindi region       20.439409     -33.150369

[100 rows x 3 columns]

In [27]:
values = []
for i in range(len(points)):
    value = img.sel(x=points.loc[i, 'POINT_X (long)'] ,y= points.loc[i, 'POINT_Y (lat)'], method='nearest')
    values.append(value)
values = numpy.array(values)
values

array([1.0000000e+20, 3.6482807e+01, 3.5750015e+01, 1.0000000e+20,
       3.4882389e+01, 1.0000000e+20, 1.0000000e+20, 1.0000000e+20,
       1.0000000e+20, 1.0000000e+20, 1.0000000e+20, 3.5724388e+01,
       1.0000000e+20, 3.6157761e+01, 3.6157761e+01, 3.6157761e+01,
       3.7045155e+01, 3.6157761e+01, 1.0000000e+20, 3.6157761e+01,
       1.0000000e+20, 3.6157761e+01, 3.6157761e+01, 3.7409683e+01,
       3.6154911e+01, 3.6154911e+01, 1.0000000e+20, 3.7409683e+01,
       3.6533703e+01, 3.6533703e+01, 1.0000000e+20, 3.6550369e+01,
       3.7210297e+01, 3.6231850e+01, 3.6324844e+01, 1.0000000e+20,
       3.8121750e+01, 1.0000000e+20, 3.6592319e+01, 3.6592319e+01,
       3.6570171e+01, 3.6169415e+01, 3.7003117e+01, 3.6175137e+01,
       3.6621761e+01, 3.6175137e+01, 3.6621761e+01, 3.6026634e+01,
       1.0000000e+20, 3.6670765e+01, 3.6897312e+01, 3.6897312e+01,
       3.7143429e+01, 3.6123966e+01, 3.6829956e+01, 3.7183754e+01,
       1.0000000e+20, 3.6893955e+01, 3.6660362e+01, 3.6206936e

### Now lets do it in a one liner!!!

In [28]:
values = img.sel(x=points['POINT_X (long)'], y=points['POINT_Y (lat)'], method="nearest").pipe(numpy.diag)
values

array([1.0000000e+20, 3.6482807e+01, 3.5750015e+01, 1.0000000e+20,
       3.4882389e+01, 1.0000000e+20, 1.0000000e+20, 1.0000000e+20,
       1.0000000e+20, 1.0000000e+20, 1.0000000e+20, 3.5724388e+01,
       1.0000000e+20, 3.6157761e+01, 3.6157761e+01, 3.6157761e+01,
       3.7045155e+01, 3.6157761e+01, 1.0000000e+20, 3.6157761e+01,
       1.0000000e+20, 3.6157761e+01, 3.6157761e+01, 3.7409683e+01,
       3.6154911e+01, 3.6154911e+01, 1.0000000e+20, 3.7409683e+01,
       3.6533703e+01, 3.6533703e+01, 1.0000000e+20, 3.6550369e+01,
       3.7210297e+01, 3.6231850e+01, 3.6324844e+01, 1.0000000e+20,
       3.8121750e+01, 1.0000000e+20, 3.6592319e+01, 3.6592319e+01,
       3.6570171e+01, 3.6169415e+01, 3.7003117e+01, 3.6175137e+01,
       3.6621761e+01, 3.6175137e+01, 3.6621761e+01, 3.6026634e+01,
       1.0000000e+20, 3.6670765e+01, 3.6897312e+01, 3.6897312e+01,
       3.7143429e+01, 3.6123966e+01, 3.6829956e+01, 3.7183754e+01,
       1.0000000e+20, 3.6893955e+01, 3.6660362e+01, 3.6206936e

## Store the values in the dataframe

No we store the values inside the data frame

In [30]:
points['SSSjfm_IPSL4X_ModPg_180x360.tif'] = values
points

/opt/conda/envs/python/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


Location__  POINT_X (long)  POINT_Y (lat)  \
0        Slovakia_Povanska_Bystrica_Manin       26.634083      39.347406   
1              Ukraine_Kolomya_Marmarosch       32.286813      39.120745   
2      Offshore W France_Armorican margin        3.730341      37.250708   
3                W Switzerland_Neuch├ótel       16.999813      36.879194   
4              North Atlantic_Flemish Cap       -0.138294      36.825156   
..                                    ...             ...            ...   
95                   Oman_Dhofar_Sallalah       39.952266     -14.264244   
96            Somalia_Bosaso & Ras Antara       36.596985     -15.086789   
97                              Iran_Khur       47.983603     -16.272461   
98  Chili_Atacama_Copiapo_Cerro Pajonales      -37.435439     -28.520510   
99                  Tanzania_Lindi region       20.439409     -33.150369   

    SSSjfm_IPSL4X_ModPg_180x360.tif  
0                      1.000000e+20  
1                      3.648281e+01  
2                      3.575002e+01  
3                      1.000000e+20  
4                      3.488239e+01  
..                              ...  
95                     1.000000e+20  
96                     1.000000e+20  
97                     3.522230e+01  
98                     1.000000e+20  
99                     1.000000e+20  

[100 rows x 4 columns]

In [31]:
points.to_csv('test.csv')

# Your Turn try doing this for `SSTjas_IPSL4X_ModPg_180x360.tif`

# Advanced

Here we get access to the points dynamically

In [32]:
from holoviews import streams
import holoviews as hv

In [33]:
# Sets up if we tap or double tap on the screen
tap = streams.SingleTap(transient=True)
double_tap = streams.DoubleTap(rename={'x': 'x2', 'y': 'y2'}, transient=True)

## Records coordinates and if we simple or double clicked

In [34]:
taps = []

def record_taps(x, y, x2, y2):
    if None not in [x,y]:
        taps.append((x, y, 1))
    elif None not in [x2, y2]:
        taps.append((x2, y2, 2))
    return hv.Points(taps, vdims='Taps')

## Plotting

Go ahead click on the map!!

In [35]:
taps_dmap = hv.DynamicMap(record_taps, streams=[tap, double_tap])

img.hvplot.image() * taps_dmap.opts(color='Taps', cmap={1: 'red', 2: 'gray'}, size=10, tools=['hover'])

:DynamicMap   []
   :Overlay
      .Image.I  :Image   [x,y]   (value)
      .Points.I :Points   [x,y]   (Taps)

## Get the results

In [36]:
taps

[(-111.32891277934229, 32.75292345942283, 1),
 (-3.1893778956213663, -10.594015316087372, 2),
 (79.83387791833212, -22.349117356903697, 1),
 (88.90364536019258, 29.07945407166773, 2),
 (9.485605061364577, 31.885281532093835, 2),
 (3.4432270312365443, 32.31896497939081, 2),
 (9.252083205127745, 30.026638186535376, 1),
 (14.068471490012408, 28.60167828827389, 1),
 (5.544923737368034, 27.672356615494664, 1),
 (-15.643647821107896, 44.401573901601964, 1)]

In [37]:
# get all the coords (remove the 1 or 2)
numpy.array(taps)[:, :2]

array([[-111.32891278,   32.75292346],
       [  -3.1893779 ,  -10.59401532],
       [  79.83387792,  -22.34911736],
       [  88.90364536,   29.07945407],
       [   9.48560506,   31.88528153],
       [   3.44322703,   32.31896498],
       [   9.25208321,   30.02663819],
       [  14.06847149,   28.60167829],
       [   5.54492374,   27.67235662],
       [ -15.64364782,   44.4015739 ]])